# Compute normalized graph distance from home



In [7]:
#import 
from models.autoencoder import *
from sklearn.manifold import TSNE
import pickle
import torch
import math
from torch import nn
import numpy as np
from matplotlib import pyplot as plt
from sklearn.decomposition import PCA
#from autoencoder.plots import *
import os
from data_generation.geom_utils import graph_distance
from data_generation.plots import *
from settings.custom_settings import CustomSettings
from data_generation.generate_trajectory import Trajectory
from copy import deepcopy
from mpl_toolkits.mplot3d import axes3d
import pandas as pd
from matplotlib.path import Path
import matplotlib.patches as patches
os.environ['KMP_DUPLICATE_LIB_OK']='True'

In [18]:
LATENT_SPACE_DIM = 3 #TODO auto fetch
GRAPH_MODEL_PATH = "./saved_models/AE_graph_exp1"
EUCL_MODEL_PATH = "./saved_models/AE_eucl_exp0"
GRAPH_EXP_NAME = "experiment1"
EUCL_EXP_NAME = "experiment0"

In [19]:
#GRAPH
with open(GRAPH_MODEL_PATH + "/test_data_traj", 'rb') as file:
    traj_test_g = pickle.load(file)
with open(GRAPH_MODEL_PATH + "/train_data_traj", 'rb') as file:
    traj_train_g = pickle.load(file)
with open(GRAPH_MODEL_PATH + "/test_maze_config", 'rb') as file:
    test_maze_config_g = pickle.load(file)
with open(GRAPH_MODEL_PATH + "/train_maze_config", 'rb') as file:
    train_maze_config_g = pickle.load(file)
    
path = "./data_generation/generated_data/" + GRAPH_EXP_NAME
with open(path + "/maze.pkl", 'rb') as file:
    maze = pickle.load(file) #Maze is common to both
with open(path + "/trajectory.pkl", 'rb') as file:
    traj_g = pickle.load(file)
    
#EUCL
with open(EUCL_MODEL_PATH + "/test_data_traj", 'rb') as file:
    traj_test_e = pickle.load(file)
with open(EUCL_MODEL_PATH + "/train_data_traj", 'rb') as file:
    traj_train_e = pickle.load(file)
with open(EUCL_MODEL_PATH + "/test_maze_config", 'rb') as file:
    test_maze_config_e = pickle.load(file)
with open(EUCL_MODEL_PATH + "/train_maze_config", 'rb') as file:
    train_maze_config_e = pickle.load(file)

#### define fct


In [20]:
def lineseg_dists(p, a, b):
    """Cartesian distance from point to line segment

    Edited to support arguments as series, from:
    https://stackoverflow.com/a/54442561/11208892

    Args:
        - p: np.array of single point, shape (2,) or 2D array, shape (x, 2)
        - a: np.array of shape (x, 2)
        - b: np.array of shape (x, 2)
    """
    # normalized tangent vectors
    d_ba = b - a
    d = np.divide(d_ba, (np.hypot(d_ba[:, 0], d_ba[:, 1])
                           .reshape(-1, 1)))

    # signed parallel distance components
    # rowwise dot products of 2D vectors
    s = np.multiply(a - p, d).sum(axis=1)
    t = np.multiply(p - b, d).sum(axis=1)

    # clamped parallel distance
    h = np.maximum.reduce([s, t, np.zeros(len(s))])

    # perpendicular distance component
    # rowwise cross products of 2D vectors  
    d_pa = p - a
    c = d_pa[:, 0] * d[:, 1] - d_pa[:, 1] * d[:, 0]

    return np.hypot(h, c)

def project(p, a, b):
    
    n = a - b
    n /= np.linalg.norm(n, 2)
    
    P = a + n*np.dot(p - a, n)
    
    return P

def graph_rel_dist(x, y, maze, cfgs_x, cfgs_y):
    #x and y are two arrays of points
    h = np.empty([maze.nb_of_trials, 2])
    c = np.empty([maze.nb_of_trials, 2])
    g0 = np.empty([maze.nb_of_trials, 2])
    g1 = np.empty([maze.nb_of_trials, 2])
    g2 = np.empty([maze.nb_of_trials, 2]) #pt/xORy/coord
    
    #extract relevant tiles for each pair of points
    for i in range(maze.nb_of_trials):
        h[i] = np.array(maze.nodeList[i]["A"])+0.5
        c[i] = np.array(maze.nodeList[i]["B"])+0.5
        g0[i] = np.array(maze.nodeList[i]["C"])+0.5
        g1[i] = np.array(maze.nodeList[i]["D"])+0.5
        g2[i] = np.array(maze.nodeList[i]["E"])+0.5

    maze_edges_v = np.array([h, g0, g1, g2])
    print(maze_edges_v.shape)
    
    #compute edge belongings for each pair of points
    d2seg_x = np.empty([x.shape[0], 4])
    d2seg_y = np.empty([y.shape[0], 4])
    
    for i in range(x.shape[0]):
        cfg_x = cfgs_x[i]
        cfg_y = cfgs_y[i]
        d2seg_x[i, :] = lineseg_dists(x[i, :], np.array([c[cfg_x], c[cfg_x], c[cfg_x], c[cfg_x]]),
                                      np.array([h[cfg_x], g0[cfg_x], g1[cfg_x], g2[cfg_x]]))
        d2seg_y[i, :] = lineseg_dists(y[i, :], np.array([c[cfg_y], c[cfg_y], c[cfg_y], c[cfg_y]]), 
                                      np.array([h[cfg_y], g0[cfg_y], g1[cfg_y], g2[cfg_y]]))
        
      
        print(str(i) + "/" + str(x.shape[0]))
    edge_bel_x = np.argmin(d2seg_x, axis = -1)
    edge_bel_y = np.argmin(d2seg_y, axis = -1)

    proj_x = np.empty([x.shape[0], 2])
    proj_y = np.empty([y.shape[0], 2])
    
    for i in range(x.shape[0]):
        cfg_x = cfgs_x[i]
        cfg_y = cfgs_y[i]
        proj_x[i, :] = project(x[i, :], maze_edges_v[edge_bel_x[i], cfg_x, :], c[cfg_x])
        proj_y[i, :] = project(y[i, :], maze_edges_v[edge_bel_y[i], cfg_y, :], c[cfg_y])
        print(str(i) + "/" + str(x.shape[0]))
    
    rel_pos_x = np.empty(x.shape[0])
    rel_pos_y = np.empty(y.shape[0])
    for i in range(x.shape[0]):
        cfg_x = cfgs_x[i]
        cfg_y = cfgs_y[i]
        rel_pos_x[i] = np.linalg.norm(c[cfg_x] - proj_x[i])/np.linalg.norm(c[cfg_x]-maze_edges_v[edge_bel_x[i], cfg_x,:])
        rel_pos_y[i] = np.linalg.norm(c[cfg_y] - proj_y[i])/np.linalg.norm(c[cfg_y]-maze_edges_v[edge_bel_y[i], cfg_y,:])
        print(str(i) + "/" + str(x.shape[0]))
    
  
    graph_rel_dist = np.empty(rel_pos_x.shape[0])

    idx_eq = np.where(edge_bel_x == edge_bel_y)[0]
    if idx_eq.size != 0:
        graph_rel_dist[idx_eq] = np.abs(rel_pos_x[idx_eq]-rel_pos_y[idx_eq])

    idx_neq = np.where(edge_bel_x != edge_bel_y)[0]
    if idx_neq.size != 0:
        graph_rel_dist[idx_neq] = np.abs(rel_pos_x[idx_neq]) + np.abs(rel_pos_y[idx_neq])


    
    return graph_rel_dist

# Compute normalized graph distance

In [21]:
#EUCLIDEAN
#maze_config_e = np.append(train_maze_config_e, test_maze_config_e, axis = 0)
#traj_tot_e = np.append(traj_train_e, traj_test_e,  axis = 0)

maze_config_e = train_maze_config_e
traj_tot_e =traj_train_e

#GRAPH
#maze_config_g =  np.append(train_maze_config_g, test_maze_config_g, axis = 0)
#traj_tot_g = np.append(traj_train_g, traj_test_g,  axis = 0)

maze_config_g =  train_maze_config_g
traj_tot_g = traj_train_g


In [22]:
#Graph dist for Eucl hyp
dge = np.empty(len(maze_config_e))
for k in range(maze.nb_of_trials): #maze config
    home = np.array(maze.nodeList[k]["A"]) + 0.5
    idx = np.where(maze_config_e == k)[0]
    cfgs_x  = np.repeat(k, len(idx))
    cfgs_y  = np.repeat(k, len(idx))
    x = traj_tot_e[idx, :]
    y = np.repeat(home[:, np.newaxis], len(idx), axis = -1).T
    
    dge[idx] = graph_rel_dist(x, y, maze, cfgs_x, cfgs_y)

(4, 25, 2)
0/2169
1/2169
2/2169
3/2169
4/2169
5/2169
6/2169
7/2169
8/2169
9/2169
10/2169
11/2169
12/2169
13/2169
14/2169
15/2169
16/2169
17/2169
18/2169
19/2169
20/2169
21/2169
22/2169
23/2169
24/2169
25/2169
26/2169
27/2169
28/2169
29/2169
30/2169
31/2169
32/2169
33/2169
34/2169
35/2169
36/2169
37/2169
38/2169
39/2169
40/2169
41/2169
42/2169
43/2169
44/2169
45/2169
46/2169
47/2169
48/2169
49/2169
50/2169
51/2169
52/2169
53/2169
54/2169
55/2169
56/2169
57/2169
58/2169
59/2169
60/2169
61/2169
62/2169
63/2169
64/2169
65/2169
66/2169
67/2169
68/2169
69/2169
70/2169
71/2169
72/2169
73/2169
74/2169
75/2169
76/2169
77/2169
78/2169
79/2169
80/2169
81/2169
82/2169
83/2169
84/2169
85/2169
86/2169
87/2169
88/2169
89/2169
90/2169
91/2169
92/2169
93/2169
94/2169
95/2169
96/2169
97/2169
98/2169
99/2169
100/2169
101/2169
102/2169
103/2169
104/2169
105/2169
106/2169
107/2169
108/2169
109/2169
110/2169
111/2169
112/2169
113/2169
114/2169
115/2169
116/2169
117/2169
118/2169
119/2169
120/2169
121/2169
1

(4, 25, 2)
0/3270
1/3270
2/3270
3/3270
4/3270
5/3270
6/3270
7/3270
8/3270
9/3270
10/3270
11/3270
12/3270
13/3270
14/3270
15/3270
16/3270
17/3270
18/3270
19/3270
20/3270
21/3270
22/3270
23/3270
24/3270
25/3270
26/3270
27/3270
28/3270
29/3270
30/3270
31/3270
32/3270
33/3270
34/3270
35/3270
36/3270
37/3270
38/3270
39/3270
40/3270
41/3270
42/3270
43/3270
44/3270
45/3270
46/3270
47/3270
48/3270
49/3270
50/3270
51/3270
52/3270
53/3270
54/3270
55/3270
56/3270
57/3270
58/3270
59/3270
60/3270
61/3270
62/3270
63/3270
64/3270
65/3270
66/3270
67/3270
68/3270
69/3270
70/3270
71/3270
72/3270
73/3270
74/3270
75/3270
76/3270
77/3270
78/3270
79/3270
80/3270
81/3270
82/3270
83/3270
84/3270
85/3270
86/3270
87/3270
88/3270
89/3270
90/3270
91/3270
92/3270
93/3270
94/3270
95/3270
96/3270
97/3270
98/3270
99/3270
100/3270
101/3270
102/3270
103/3270
104/3270
105/3270
106/3270
107/3270
108/3270
109/3270
110/3270
111/3270
112/3270
113/3270
114/3270
115/3270
116/3270
117/3270
118/3270
119/3270
120/3270
121/3270
1

1695/3270
1696/3270
1697/3270
1698/3270
1699/3270
1700/3270
1701/3270
1702/3270
1703/3270
1704/3270
1705/3270
1706/3270
1707/3270
1708/3270
1709/3270
1710/3270
1711/3270
1712/3270
1713/3270
1714/3270
1715/3270
1716/3270
1717/3270
1718/3270
1719/3270
1720/3270
1721/3270
1722/3270
1723/3270
1724/3270
1725/3270
1726/3270
1727/3270
1728/3270
1729/3270
1730/3270
1731/3270
1732/3270
1733/3270
1734/3270
1735/3270
1736/3270
1737/3270
1738/3270
1739/3270
1740/3270
1741/3270
1742/3270
1743/3270
1744/3270
1745/3270
1746/3270
1747/3270
1748/3270
1749/3270
1750/3270
1751/3270
1752/3270
1753/3270
1754/3270
1755/3270
1756/3270
1757/3270
1758/3270
1759/3270
1760/3270
1761/3270
1762/3270
1763/3270
1764/3270
1765/3270
1766/3270
1767/3270
1768/3270
1769/3270
1770/3270
1771/3270
1772/3270
1773/3270
1774/3270
1775/3270
1776/3270
1777/3270
1778/3270
1779/3270
1780/3270
1781/3270
1782/3270
1783/3270
1784/3270
1785/3270
1786/3270
1787/3270
1788/3270
1789/3270
1790/3270
1791/3270
1792/3270
1793/3270
1794/3270


2064/2216
2065/2216
2066/2216
2067/2216
2068/2216
2069/2216
2070/2216
2071/2216
2072/2216
2073/2216
2074/2216
2075/2216
2076/2216
2077/2216
2078/2216
2079/2216
2080/2216
2081/2216
2082/2216
2083/2216
2084/2216
2085/2216
2086/2216
2087/2216
2088/2216
2089/2216
2090/2216
2091/2216
2092/2216
2093/2216
2094/2216
2095/2216
2096/2216
2097/2216
2098/2216
2099/2216
2100/2216
2101/2216
2102/2216
2103/2216
2104/2216
2105/2216
2106/2216
2107/2216
2108/2216
2109/2216
2110/2216
2111/2216
2112/2216
2113/2216
2114/2216
2115/2216
2116/2216
2117/2216
2118/2216
2119/2216
2120/2216
2121/2216
2122/2216
2123/2216
2124/2216
2125/2216
2126/2216
2127/2216
2128/2216
2129/2216
2130/2216
2131/2216
2132/2216
2133/2216
2134/2216
2135/2216
2136/2216
2137/2216
2138/2216
2139/2216
2140/2216
2141/2216
2142/2216
2143/2216
2144/2216
2145/2216
2146/2216
2147/2216
2148/2216
2149/2216
2150/2216
2151/2216
2152/2216
2153/2216
2154/2216
2155/2216
2156/2216
2157/2216
2158/2216
2159/2216
2160/2216
2161/2216
2162/2216
2163/2216


1754/2045
1755/2045
1756/2045
1757/2045
1758/2045
1759/2045
1760/2045
1761/2045
1762/2045
1763/2045
1764/2045
1765/2045
1766/2045
1767/2045
1768/2045
1769/2045
1770/2045
1771/2045
1772/2045
1773/2045
1774/2045
1775/2045
1776/2045
1777/2045
1778/2045
1779/2045
1780/2045
1781/2045
1782/2045
1783/2045
1784/2045
1785/2045
1786/2045
1787/2045
1788/2045
1789/2045
1790/2045
1791/2045
1792/2045
1793/2045
1794/2045
1795/2045
1796/2045
1797/2045
1798/2045
1799/2045
1800/2045
1801/2045
1802/2045
1803/2045
1804/2045
1805/2045
1806/2045
1807/2045
1808/2045
1809/2045
1810/2045
1811/2045
1812/2045
1813/2045
1814/2045
1815/2045
1816/2045
1817/2045
1818/2045
1819/2045
1820/2045
1821/2045
1822/2045
1823/2045
1824/2045
1825/2045
1826/2045
1827/2045
1828/2045
1829/2045
1830/2045
1831/2045
1832/2045
1833/2045
1834/2045
1835/2045
1836/2045
1837/2045
1838/2045
1839/2045
1840/2045
1841/2045
1842/2045
1843/2045
1844/2045
1845/2045
1846/2045
1847/2045
1848/2045
1849/2045
1850/2045
1851/2045
1852/2045
1853/2045


...

2640/2895
2641/2895
2642/2895
2643/2895
2644/2895
2645/2895
2646/2895
2647/2895
2648/2895
2649/2895
2650/2895
2651/2895
2652/2895
2653/2895
2654/2895
2655/2895
2656/2895
2657/2895
2658/2895
2659/2895
2660/2895
2661/2895
2662/2895
2663/2895
2664/2895
2665/2895
2666/2895
2667/2895
2668/2895
2669/2895
2670/2895
2671/2895
2672/2895
2673/2895
2674/2895
2675/2895
2676/2895
2677/2895
2678/2895
2679/2895
2680/2895
2681/2895
2682/2895
2683/2895
2684/2895
2685/2895
2686/2895
2687/2895
2688/2895
2689/2895
2690/2895
2691/2895
2692/2895
2693/2895
2694/2895
2695/2895
2696/2895
2697/2895
2698/2895
2699/2895
2700/2895
2701/2895
2702/2895
2703/2895
2704/2895
2705/2895
2706/2895
2707/2895
2708/2895
2709/2895
2710/2895
2711/2895
2712/2895
2713/2895
2714/2895
2715/2895
2716/2895
2717/2895
2718/2895
2719/2895
2720/2895
2721/2895
2722/2895
2723/2895
2724/2895
2725/2895
2726/2895
2727/2895
2728/2895
2729/2895
2730/2895
2731/2895
2732/2895
2733/2895
2734/2895
2735/2895
2736/2895
2737/2895
2738/2895
2739/2895


2139/2451
2140/2451
2141/2451
2142/2451
2143/2451
2144/2451
2145/2451
2146/2451
2147/2451
2148/2451
2149/2451
2150/2451
2151/2451
2152/2451
2153/2451
2154/2451
2155/2451
2156/2451
2157/2451
2158/2451
2159/2451
2160/2451
2161/2451
2162/2451
2163/2451
2164/2451
2165/2451
2166/2451
2167/2451
2168/2451
2169/2451
2170/2451
2171/2451
2172/2451
2173/2451
2174/2451
2175/2451
2176/2451
2177/2451
2178/2451
2179/2451
2180/2451
2181/2451
2182/2451
2183/2451
2184/2451
2185/2451
2186/2451
2187/2451
2188/2451
2189/2451
2190/2451
2191/2451
2192/2451
2193/2451
2194/2451
2195/2451
2196/2451
2197/2451
2198/2451
2199/2451
2200/2451
2201/2451
2202/2451
2203/2451
2204/2451
2205/2451
2206/2451
2207/2451
2208/2451
2209/2451
2210/2451
2211/2451
2212/2451
2213/2451
2214/2451
2215/2451
2216/2451
2217/2451
2218/2451
2219/2451
2220/2451
2221/2451
2222/2451
2223/2451
2224/2451
2225/2451
2226/2451
2227/2451
2228/2451
2229/2451
2230/2451
2231/2451
2232/2451
2233/2451
2234/2451
2235/2451
2236/2451
2237/2451
2238/2451


1498/2739
1499/2739
1500/2739
1501/2739
1502/2739
1503/2739
1504/2739
1505/2739
1506/2739
1507/2739
1508/2739
1509/2739
1510/2739
1511/2739
1512/2739
1513/2739
1514/2739
1515/2739
1516/2739
1517/2739
1518/2739
1519/2739
1520/2739
1521/2739
1522/2739
1523/2739
1524/2739
1525/2739
1526/2739
1527/2739
1528/2739
1529/2739
1530/2739
1531/2739
1532/2739
1533/2739
1534/2739
1535/2739
1536/2739
1537/2739
1538/2739
1539/2739
1540/2739
1541/2739
1542/2739
1543/2739
1544/2739
1545/2739
1546/2739
1547/2739
1548/2739
1549/2739
1550/2739
1551/2739
1552/2739
1553/2739
1554/2739
1555/2739
1556/2739
1557/2739
1558/2739
1559/2739
1560/2739
1561/2739
1562/2739
1563/2739
1564/2739
1565/2739
1566/2739
1567/2739
1568/2739
1569/2739
1570/2739
1571/2739
1572/2739
1573/2739
1574/2739
1575/2739
1576/2739
1577/2739
1578/2739
1579/2739
1580/2739
1581/2739
1582/2739
1583/2739
1584/2739
1585/2739
1586/2739
1587/2739
1588/2739
1589/2739
1590/2739
1591/2739
1592/2739
1593/2739
1594/2739
1595/2739
1596/2739
1597/2739


231/2686
232/2686
233/2686
234/2686
235/2686
236/2686
237/2686
238/2686
239/2686
240/2686
241/2686
242/2686
243/2686
244/2686
245/2686
246/2686
247/2686
248/2686
249/2686
250/2686
251/2686
252/2686
253/2686
254/2686
255/2686
256/2686
257/2686
258/2686
259/2686
260/2686
261/2686
262/2686
263/2686
264/2686
265/2686
266/2686
267/2686
268/2686
269/2686
270/2686
271/2686
272/2686
273/2686
274/2686
275/2686
276/2686
277/2686
278/2686
279/2686
280/2686
281/2686
282/2686
283/2686
284/2686
285/2686
286/2686
287/2686
288/2686
289/2686
290/2686
291/2686
292/2686
293/2686
294/2686
295/2686
296/2686
297/2686
298/2686
299/2686
300/2686
301/2686
302/2686
303/2686
304/2686
305/2686
306/2686
307/2686
308/2686
309/2686
310/2686
311/2686
312/2686
313/2686
314/2686
315/2686
316/2686
317/2686
318/2686
319/2686
320/2686
321/2686
322/2686
323/2686
324/2686
325/2686
326/2686
327/2686
328/2686
329/2686
330/2686
331/2686
332/2686
333/2686
334/2686
335/2686
336/2686
337/2686
338/2686
339/2686
340/2686
341/2686
3

155/2686
156/2686
157/2686
158/2686
159/2686
160/2686
161/2686
162/2686
163/2686
164/2686
165/2686
166/2686
167/2686
168/2686
169/2686
170/2686
171/2686
172/2686
173/2686
174/2686
175/2686
176/2686
177/2686
178/2686
179/2686
180/2686
181/2686
182/2686
183/2686
184/2686
185/2686
186/2686
187/2686
188/2686
189/2686
190/2686
191/2686
192/2686
193/2686
194/2686
195/2686
196/2686
197/2686
198/2686
199/2686
200/2686
201/2686
202/2686
203/2686
204/2686
205/2686
206/2686
207/2686
208/2686
209/2686
210/2686
211/2686
212/2686
213/2686
214/2686
215/2686
216/2686
217/2686
218/2686
219/2686
220/2686
221/2686
222/2686
223/2686
224/2686
225/2686
226/2686
227/2686
228/2686
229/2686
230/2686
231/2686
232/2686
233/2686
234/2686
235/2686
236/2686
237/2686
238/2686
239/2686
240/2686
241/2686
242/2686
243/2686
244/2686
245/2686
246/2686
247/2686
248/2686
249/2686
250/2686
251/2686
252/2686
253/2686
254/2686
255/2686
256/2686
257/2686
258/2686
259/2686
260/2686
261/2686
262/2686
263/2686
264/2686
265/2686
2

In [23]:
with open('./dge', 'wb') as outp:
    pickle.dump(dge, outp, pickle.HIGHEST_PROTOCOL)


In [24]:
#Graph dist for Eucl hyp
dgg = np.empty(len(maze_config_g))
for k in range(maze.nb_of_trials): #maze config
    home = np.array(maze.nodeList[k]["A"]) + 0.5
    idx = np.where(maze_config_g == k)[0]
    cfgs_x  = np.repeat(k, len(idx))
    cfgs_y  = np.repeat(k, len(idx))
    x = traj_tot_g[idx, :]
    y = np.repeat(home[:, np.newaxis], len(idx), axis = -1).T
    
    dgg[idx] = graph_rel_dist(x, y, maze, cfgs_x, cfgs_y)


(4, 25, 2)
0/2352
1/2352
2/2352
3/2352
4/2352
5/2352
6/2352
7/2352
8/2352
9/2352
10/2352
11/2352
12/2352
13/2352
14/2352
15/2352
16/2352
17/2352
18/2352
19/2352
20/2352
21/2352
22/2352
23/2352
24/2352
25/2352
26/2352
27/2352
28/2352
29/2352
30/2352
31/2352
32/2352
33/2352
34/2352
35/2352
36/2352
37/2352
38/2352
39/2352
40/2352
41/2352
42/2352
43/2352
44/2352
45/2352
46/2352
47/2352
48/2352
49/2352
50/2352
51/2352
52/2352
53/2352
54/2352
55/2352
56/2352
57/2352
58/2352
59/2352
60/2352
61/2352
62/2352
63/2352
64/2352
65/2352
66/2352
67/2352
68/2352
69/2352
70/2352
71/2352
72/2352
73/2352
74/2352
75/2352
76/2352
77/2352
78/2352
79/2352
80/2352
81/2352
82/2352
83/2352
84/2352
85/2352
86/2352
87/2352
88/2352
89/2352
90/2352
91/2352
92/2352
93/2352
94/2352
95/2352
96/2352
97/2352
98/2352
99/2352
100/2352
101/2352
102/2352
103/2352
104/2352
105/2352
106/2352
107/2352
108/2352
109/2352
110/2352
111/2352
112/2352
113/2352
114/2352
115/2352
116/2352
117/2352
118/2352
119/2352
120/2352
121/2352
1

0/2352
1/2352
2/2352
3/2352
4/2352
5/2352
6/2352
7/2352
8/2352
9/2352
10/2352
11/2352
12/2352
13/2352
14/2352
15/2352
16/2352
17/2352
18/2352
19/2352
20/2352
21/2352
22/2352
23/2352
24/2352
25/2352
26/2352
27/2352
28/2352
29/2352
30/2352
31/2352
32/2352
33/2352
34/2352
35/2352
36/2352
37/2352
38/2352
39/2352
40/2352
41/2352
42/2352
43/2352
44/2352
45/2352
46/2352
47/2352
48/2352
49/2352
50/2352
51/2352
52/2352
53/2352
54/2352
55/2352
56/2352
57/2352
58/2352
59/2352
60/2352
61/2352
62/2352
63/2352
64/2352
65/2352
66/2352
67/2352
68/2352
69/2352
70/2352
71/2352
72/2352
73/2352
74/2352
75/2352
76/2352
77/2352
78/2352
79/2352
80/2352
81/2352
82/2352
83/2352
84/2352
85/2352
86/2352
87/2352
88/2352
89/2352
90/2352
91/2352
92/2352
93/2352
94/2352
95/2352
96/2352
97/2352
98/2352
99/2352
100/2352
101/2352
102/2352
103/2352
104/2352
105/2352
106/2352
107/2352
108/2352
109/2352
110/2352
111/2352
112/2352
113/2352
114/2352
115/2352
116/2352
117/2352
118/2352
119/2352
120/2352
121/2352
122/2352
123

831/2352
832/2352
833/2352
834/2352
835/2352
836/2352
837/2352
838/2352
839/2352
840/2352
841/2352
842/2352
843/2352
844/2352
845/2352
846/2352
847/2352
848/2352
849/2352
850/2352
851/2352
852/2352
853/2352
854/2352
855/2352
856/2352
857/2352
858/2352
859/2352
860/2352
861/2352
862/2352
863/2352
864/2352
865/2352
866/2352
867/2352
868/2352
869/2352
870/2352
871/2352
872/2352
873/2352
874/2352
875/2352
876/2352
877/2352
878/2352
879/2352
880/2352
881/2352
882/2352
883/2352
884/2352
885/2352
886/2352
887/2352
888/2352
889/2352
890/2352
891/2352
892/2352
893/2352
894/2352
895/2352
896/2352
897/2352
898/2352
899/2352
900/2352
901/2352
902/2352
903/2352
904/2352
905/2352
906/2352
907/2352
908/2352
909/2352
910/2352
911/2352
912/2352
913/2352
914/2352
915/2352
916/2352
917/2352
918/2352
919/2352
920/2352
921/2352
922/2352
923/2352
924/2352
925/2352
926/2352
927/2352
928/2352
929/2352
930/2352
931/2352
932/2352
933/2352
934/2352
935/2352
936/2352
937/2352
938/2352
939/2352
940/2352
941/2352
9

1224/3326
1225/3326
1226/3326
1227/3326
1228/3326
1229/3326
1230/3326
1231/3326
1232/3326
1233/3326
1234/3326
1235/3326
1236/3326
1237/3326
1238/3326
1239/3326
1240/3326
1241/3326
1242/3326
1243/3326
1244/3326
1245/3326
1246/3326
1247/3326
1248/3326
1249/3326
1250/3326
1251/3326
1252/3326
1253/3326
1254/3326
1255/3326
1256/3326
1257/3326
1258/3326
1259/3326
1260/3326
1261/3326
1262/3326
1263/3326
1264/3326
1265/3326
1266/3326
1267/3326
1268/3326
1269/3326
1270/3326
1271/3326
1272/3326
1273/3326
1274/3326
1275/3326
1276/3326
1277/3326
1278/3326
1279/3326
1280/3326
1281/3326
1282/3326
1283/3326
1284/3326
1285/3326
1286/3326
1287/3326
1288/3326
1289/3326
1290/3326
1291/3326
1292/3326
1293/3326
1294/3326
1295/3326
1296/3326
1297/3326
1298/3326
1299/3326
1300/3326
1301/3326
1302/3326
1303/3326
1304/3326
1305/3326
1306/3326
1307/3326
1308/3326
1309/3326
1310/3326
1311/3326
1312/3326
1313/3326
1314/3326
1315/3326
1316/3326
1317/3326
1318/3326
1319/3326
1320/3326
1321/3326
1322/3326
1323/3326


262/3326
263/3326
264/3326
265/3326
266/3326
267/3326
268/3326
269/3326
270/3326
271/3326
272/3326
273/3326
274/3326
275/3326
276/3326
277/3326
278/3326
279/3326
280/3326
281/3326
282/3326
283/3326
284/3326
285/3326
286/3326
287/3326
288/3326
289/3326
290/3326
291/3326
292/3326
293/3326
294/3326
295/3326
296/3326
297/3326
298/3326
299/3326
300/3326
301/3326
302/3326
303/3326
304/3326
305/3326
306/3326
307/3326
308/3326
309/3326
310/3326
311/3326
312/3326
313/3326
314/3326
315/3326
316/3326
317/3326
318/3326
319/3326
320/3326
321/3326
322/3326
323/3326
324/3326
325/3326
326/3326
327/3326
328/3326
329/3326
330/3326
331/3326
332/3326
333/3326
334/3326
335/3326
336/3326
337/3326
338/3326
339/3326
340/3326
341/3326
342/3326
343/3326
344/3326
345/3326
346/3326
347/3326
348/3326
349/3326
350/3326
351/3326
352/3326
353/3326
354/3326
355/3326
356/3326
357/3326
358/3326
359/3326
360/3326
361/3326
362/3326
363/3326
364/3326
365/3326
366/3326
367/3326
368/3326
369/3326
370/3326
371/3326
372/3326
3

...

203/2449
204/2449
205/2449
206/2449
207/2449
208/2449
209/2449
210/2449
211/2449
212/2449
213/2449
214/2449
215/2449
216/2449
217/2449
218/2449
219/2449
220/2449
221/2449
222/2449
223/2449
224/2449
225/2449
226/2449
227/2449
228/2449
229/2449
230/2449
231/2449
232/2449
233/2449
234/2449
235/2449
236/2449
237/2449
238/2449
239/2449
240/2449
241/2449
242/2449
243/2449
244/2449
245/2449
246/2449
247/2449
248/2449
249/2449
250/2449
251/2449
252/2449
253/2449
254/2449
255/2449
256/2449
257/2449
258/2449
259/2449
260/2449
261/2449
262/2449
263/2449
264/2449
265/2449
266/2449
267/2449
268/2449
269/2449
270/2449
271/2449
272/2449
273/2449
274/2449
275/2449
276/2449
277/2449
278/2449
279/2449
280/2449
281/2449
282/2449
283/2449
284/2449
285/2449
286/2449
287/2449
288/2449
289/2449
290/2449
291/2449
292/2449
293/2449
294/2449
295/2449
296/2449
297/2449
298/2449
299/2449
300/2449
301/2449
302/2449
303/2449
304/2449
305/2449
306/2449
307/2449
308/2449
309/2449
310/2449
311/2449
312/2449
313/2449
3

1322/2449
1323/2449
1324/2449
1325/2449
1326/2449
1327/2449
1328/2449
1329/2449
1330/2449
1331/2449
1332/2449
1333/2449
1334/2449
1335/2449
1336/2449
1337/2449
1338/2449
1339/2449
1340/2449
1341/2449
1342/2449
1343/2449
1344/2449
1345/2449
1346/2449
1347/2449
1348/2449
1349/2449
1350/2449
1351/2449
1352/2449
1353/2449
1354/2449
1355/2449
1356/2449
1357/2449
1358/2449
1359/2449
1360/2449
1361/2449
1362/2449
1363/2449
1364/2449
1365/2449
1366/2449
1367/2449
1368/2449
1369/2449
1370/2449
1371/2449
1372/2449
1373/2449
1374/2449
1375/2449
1376/2449
1377/2449
1378/2449
1379/2449
1380/2449
1381/2449
1382/2449
1383/2449
1384/2449
1385/2449
1386/2449
1387/2449
1388/2449
1389/2449
1390/2449
1391/2449
1392/2449
1393/2449
1394/2449
1395/2449
1396/2449
1397/2449
1398/2449
1399/2449
1400/2449
1401/2449
1402/2449
1403/2449
1404/2449
1405/2449
1406/2449
1407/2449
1408/2449
1409/2449
1410/2449
1411/2449
1412/2449
1413/2449
1414/2449
1415/2449
1416/2449
1417/2449
1418/2449
1419/2449
1420/2449
1421/2449


891/2826
892/2826
893/2826
894/2826
895/2826
896/2826
897/2826
898/2826
899/2826
900/2826
901/2826
902/2826
903/2826
904/2826
905/2826
906/2826
907/2826
908/2826
909/2826
910/2826
911/2826
912/2826
913/2826
914/2826
915/2826
916/2826
917/2826
918/2826
919/2826
920/2826
921/2826
922/2826
923/2826
924/2826
925/2826
926/2826
927/2826
928/2826
929/2826
930/2826
931/2826
932/2826
933/2826
934/2826
935/2826
936/2826
937/2826
938/2826
939/2826
940/2826
941/2826
942/2826
943/2826
944/2826
945/2826
946/2826
947/2826
948/2826
949/2826
950/2826
951/2826
952/2826
953/2826
954/2826
955/2826
956/2826
957/2826
958/2826
959/2826
960/2826
961/2826
962/2826
963/2826
964/2826
965/2826
966/2826
967/2826
968/2826
969/2826
970/2826
971/2826
972/2826
973/2826
974/2826
975/2826
976/2826
977/2826
978/2826
979/2826
980/2826
981/2826
982/2826
983/2826
984/2826
985/2826
986/2826
987/2826
988/2826
989/2826
990/2826
991/2826
992/2826
993/2826
994/2826
995/2826
996/2826
997/2826
998/2826
999/2826
1000/2826
1001/2826

2354/2695
2355/2695
2356/2695
2357/2695
2358/2695
2359/2695
2360/2695
2361/2695
2362/2695
2363/2695
2364/2695
2365/2695
2366/2695
2367/2695
2368/2695
2369/2695
2370/2695
2371/2695
2372/2695
2373/2695
2374/2695
2375/2695
2376/2695
2377/2695
2378/2695
2379/2695
2380/2695
2381/2695
2382/2695
2383/2695
2384/2695
2385/2695
2386/2695
2387/2695
2388/2695
2389/2695
2390/2695
2391/2695
2392/2695
2393/2695
2394/2695
2395/2695
2396/2695
2397/2695
2398/2695
2399/2695
2400/2695
2401/2695
2402/2695
2403/2695
2404/2695
2405/2695
2406/2695
2407/2695
2408/2695
2409/2695
2410/2695
2411/2695
2412/2695
2413/2695
2414/2695
2415/2695
2416/2695
2417/2695
2418/2695
2419/2695
2420/2695
2421/2695
2422/2695
2423/2695
2424/2695
2425/2695
2426/2695
2427/2695
2428/2695
2429/2695
2430/2695
2431/2695
2432/2695
2433/2695
2434/2695
2435/2695
2436/2695
2437/2695
2438/2695
2439/2695
2440/2695
2441/2695
2442/2695
2443/2695
2444/2695
2445/2695
2446/2695
2447/2695
2448/2695
2449/2695
2450/2695
2451/2695
2452/2695
2453/2695


2132/2695
2133/2695
2134/2695
2135/2695
2136/2695
2137/2695
2138/2695
2139/2695
2140/2695
2141/2695
2142/2695
2143/2695
2144/2695
2145/2695
2146/2695
2147/2695
2148/2695
2149/2695
2150/2695
2151/2695
2152/2695
2153/2695
2154/2695
2155/2695
2156/2695
2157/2695
2158/2695
2159/2695
2160/2695
2161/2695
2162/2695
2163/2695
2164/2695
2165/2695
2166/2695
2167/2695
2168/2695
2169/2695
2170/2695
2171/2695
2172/2695
2173/2695
2174/2695
2175/2695
2176/2695
2177/2695
2178/2695
2179/2695
2180/2695
2181/2695
2182/2695
2183/2695
2184/2695
2185/2695
2186/2695
2187/2695
2188/2695
2189/2695
2190/2695
2191/2695
2192/2695
2193/2695
2194/2695
2195/2695
2196/2695
2197/2695
2198/2695
2199/2695
2200/2695
2201/2695
2202/2695
2203/2695
2204/2695
2205/2695
2206/2695
2207/2695
2208/2695
2209/2695
2210/2695
2211/2695
2212/2695
2213/2695
2214/2695
2215/2695
2216/2695
2217/2695
2218/2695
2219/2695
2220/2695
2221/2695
2222/2695
2223/2695
2224/2695
2225/2695
2226/2695
2227/2695
2228/2695
2229/2695
2230/2695
2231/2695


In [25]:
with open('./dgg', 'wb') as outp:
    pickle.dump(dgg, outp, pickle.HIGHEST_PROTOCOL)